# {class}`~tvm.contrib.msc.framework.tensorflow.runtime.TensorflowRunner`

In [1]:
%cd ..
from pathlib import Path

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

/media/pc/data/lxw/ai/tvm-book/doc/tutorials/msc


构建前端模型：

In [2]:
from tvm.contrib.msc.framework.tensorflow import tf_v1
import tvm


def _get_tf_graph():
    """Get tensorflow graphdef"""

    # pylint: disable=import-outside-toplevel
    try:
        import tvm.relay.testing.tf as tf_testing

        tf_graph = tf_v1.Graph()
        with tf_graph.as_default():
            graph_def = tf_testing.get_workload(
                "https://storage.googleapis.com/mobilenet_v2/checkpoints/mobilenet_v2_1.4_224.tgz",
                "mobilenet_v2_1.4_224_frozen.pb",
            )
            # Call the utility to import the graph definition into default graph.
            graph_def = tf_testing.ProcessGraphDefParam(graph_def)
        return tf_graph, graph_def
    except:  # pylint: disable=bare-except
        print("please install tensorflow package")
        return None, None


2024-12-31 17:42:47.206712: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-12-31 17:42:47.504784: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-12-31 17:42:47.619618: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-12-31 17:42:48.380815: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-12-31 17:43:08.227733: W tensorflow/compiler/tf2

In [3]:
import numpy as np
from tvm.contrib.msc.framework.tensorflow.frontend import from_tensorflow
from tvm.contrib.msc.framework.tensorflow.runtime import TensorflowRunner
from tvm.contrib.msc.core import utils as msc_utils


tf_graph, graph_def = _get_tf_graph()
if tf_graph and graph_def:
    path = f"{temp_dir}/test_runner_tf"
    workspace = msc_utils.set_workspace(msc_utils.msc_dir(path, keep_history=False))
    log_path = workspace.relpath("MSC_LOG", keep_history=False)
    msc_utils.set_global_logger("critical", log_path)
    data = np.random.uniform(size=(1, 224, 224, 3)).astype("float32")
    out_name = "MobilenetV2/Predictions/Reshape_1:0"
    # get golden
    with tf_v1.Session(graph=tf_graph) as sess:
        golden = sess.run([out_name], {"input:0": data})
    # get outputs
    shape_dict = {"input": data.shape}
    mod, _ = from_tensorflow(graph_def, shape_dict, [out_name], as_msc=False)
    runner = TensorflowRunner(mod)
    runner.build()
    outputs = runner.run([data], ret_type="list")
    workspace.destory()
    for gol_r, out_r in zip(golden, outputs):
        tvm.testing.assert_allclose(gol_r, msc_utils.cast_array(out_r), atol=1e-3, rtol=1e-3)


Instructions for updating:
Use tf.gfile.GFile.


2024-12-31 17:43:35.660493: I tensorflow/core/common_runtime/gpu/gpu_device.cc:2021] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 21128 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 3090, pci bus id: 0000:03:00.0, compute capability: 8.6
2024-12-31 17:43:35.661150: I tensorflow/core/common_runtime/gpu/gpu_device.cc:2021] Created device /job:localhost/replica:0/task:0/device:GPU:1 with 9796 MB memory:  -> device: 1, name: NVIDIA GeForce RTX 2080 Ti, pci bus id: 0000:81:00.0, compute capability: 7.5
2024-12-31 17:43:35.750451: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:388] MLIR V1 optimization pass is not enabled
2024-12-31 17:43:37.934376: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:531] Loaded cuDNN version 8907
W0000 00:00:1735638218.239880   29375 gpu_timer.cc:114] Skipping the delay kernel, measurement accuracy will be reduced
W0000 00:00:1735638218.328986   29375 gpu_timer.cc:114] Skipping the delay kernel, measurement accurac

AttributeError: `batch_normalization` is not available with Keras 3.